<a href="https://colab.research.google.com/github/Eliokay/Visualizing-US-School-Shootings-Data/blob/main/Visualizing_US_School_Shootings_using_Interactive_Maps.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
!pip install osmnx
import pandas as pd
import altair as alt

from vega_datasets import data

import geopandas as gpd
import osmnx as ox
import folium
from folium import plugins



     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.3/104.3 kB 695.7 kB/s eta 0:00:00


In [3]:
df = pd.read_csv('https://raw.githubusercontent.com/washingtonpost/data-school-shootings/master/school-shootings-data.csv')

df = df.dropna(subset=['lat','long'])
df.head()

uid nces_school_id                  school_name  nces_district_id  \
0    1   080480000707        Columbine High School          804800.0   
1    2   220054000422  Scotlandville Middle School         2200540.0   
2    3   130441001591         Heritage High School         1304410.0   
3    4   421899003847     John Bartram High School         4218990.0   
4    5   250279000225       Dorchester High School         2502790.0   

                          district_name       date school_year  year  \
0                  Jefferson County R-1  4/20/1999   1998-1999  1999   
1  East Baton Rouge Parish School Board  4/22/1999   1998-1999  1999   
2                       Rockdale County  5/20/1999   1998-1999  1999   
3                  Philadelphia City SD  10/4/1999   1999-2000  1999   
4                                Boston  11/3/1999   1999-2000  1999   

       time day_of_week  ...        lat        long staffing low_grade  \
0  11:19 AM     Tuesday  ...  39.603910 -105.075000     89.6         9   
1  12:30 PM    Thursday  ...  30.529958  -91.169966     39.0         6   
2   8:03 AM    Thursday  ...  33.626922  -84.047960     84.0         9   
3  10:00 AM      Monday  ...  39.921509  -75.234108     41.0         9   
4   7:40 AM   Wednesday  ...  42.285268  -71.075901      NaN         9   

   high_grade  lunch                   county state_fips  county_fips ulocale  
0          12     41         Jefferson County          8         8059    21.0  
1           8    495  East Baton Rouge Parish         22        22033    12.0  
2          12    125          Rockdale County         13        13247    21.0  
3          12   2007      Philadelphia County         42        42101    11.0  
4          12    543           Suffolk County         25        25025    11.0  

[5 rows x 50 columns]

##1. A static Point map made in Altair Displaying School Shootings Across the US.

In [4]:
states = alt.topo_feature(data.us_10m.url, 'states')

choropleth = alt.Chart(states).mark_geoshape(stroke='black').encode(
    alt.Color("casualties:Q",bin=True, title='Casualties'),
    tooltip='state:N'
).transform_lookup(
    lookup='id',
    from_=alt.LookupData(df, 'state_fips', ["casualties","state"]),
).project(
    type='albersUsa'
).properties(
    width=800,
    height=500,
    title='Number of Casualties in School Shootings Across the US'
)

choropleth.configure_title(
     fontSize=25,
     anchor='middle',
).configure_header(
    labelFontSize=20
).configure_axis(
    titleFontSize=18,
    labelFontSize=18,
    gridOpacity=0.2

)

alt.Chart(...)

Iteration 1

In [5]:

m = folium.Map(width=800,height=800,
               location=[38.922338, -77.029756],
               tiles='cartodbpositron',
               zoom_start=3, control_scale=True)

# folium.map.Marker(
#     location=[47.6, -122.3],  # Adjust the location as needed
#     icon=None,
#     popup=folium.Popup("<b>Point Map of School Shootings Across the US</b>", parse_html=True),
# ).add_to(m)

for idx, row in df.iterrows():

    lon = row['long']
    lat = row['lat']


    folium.Marker(location=[lat, lon]).add_to(m)
m

Iteration 2: Point icons were changed to show severity of the school shootings. blue points indicates less that 3 casualties and red points indicated greater than 3.

In [22]:
m = folium.Map(width=800,height=800,
               location=[47.493015, -122.233115],
               tiles='cartodbpositron',
               zoom_start=3, control_scale=True)

for idx, row in df.iterrows():
    # Get lat and lon of points
    lon = row['long']
    lat = row['lat']


    # get name for tooltip
    name = row['casualties']

    # change icon based on tree height
    if row['casualties'] > 3:
        icon = folium.Icon(icon = 'fa-user-injured', color = 'red', prefix = 'fa')
    else:
        icon = folium.Icon(icon = 'fa-user-injured', color = 'blue', prefix='fa')

    # Add marker to the map
    x = folium.Marker(location=[lat, lon],
                  tooltip=name,
                  icon=icon
    ).add_to(m)

m

Iteration 3: This map is modifies to add cluster points to the follium. I also added a filter at the top left corner to filter the points by the gender of shooters.

In [23]:
m = folium.Map(width=800,height=800,
               location=[47.6, -122.3],
               tiles='cartodbpositron',
               zoom_start=3, control_scale=True)
marker_cluster = plugins.MarkerCluster().add_to(m)

for idx, row in df.iterrows():
    # Get lat and lon of points
    lon = row['long']
    lat = row['lat']


    # get name for tooltip
    name = row['casualties']

    # change icon based on tree height
    if row['casualties'] > 3:
        icon = folium.Icon(icon = 'fa-user-injured', color = 'red', prefix = 'fa')
    else:
        icon = folium.Icon(icon = 'fa-user-injured', color = 'blue', prefix='fa')
    if row['gender_shooter1']=='m':
        Shooter_gender = 'Male Shooter'
    else:
        Shooter_gender = 'Female Shooter'

    # Add marker to the map
    folium.Marker(location=[lat, lon],
                  tooltip=name,
                  icon=icon,
                  tags=[Shooter_gender]
   ).add_to(marker_cluster)

categories = ['Male Shooter','Female Shooter']
plugins.TagFilterButton(categories).add_to(m)

m

Iteration 4: This contains a histogram showing the count of the number of casualties for one point on the map

In [24]:
hist = alt.Chart(df).mark_bar().encode(
        x=alt.X("casualties:Q", bin=True),
        y="count()")

vega_lite = folium.VegaLite(
    hist,
    width="100%",
    height="100%",
)
m = folium.Map(width=800,height=800,
               location=[42.38469, -83.11269],
               tiles='cartodbpositron',
               zoom_start=3, control_scale=True)

# for idx, row in df.iterrows():
#     # Get lat and lon of points
lon = row['long']
lat = row['lat']

marker = folium.Marker(location=[lat, lon]).add_to(m)

popup = folium.Popup()

vega_lite.add_to(popup)
popup.add_to(marker)

marker.add_to(m)

m

/usr/local/lib/python3.10/dist-packages/altair/utils/schemapi.py:97: DeprecationWarning: jsonschema.RefResolver is deprecated as of v4.18.0, in favor of the https://github.com/python-jsonschema/referencing library, which provides more compliant referencing behavior as well as more flexible APIs for customization. A future release will remove RefResolver. Please file a feature request (on referencing) if you are missing an API for the kind of customization you need.
  resolver = jsonschema.RefResolver.from_schema(root or schema)
/usr/local/lib/python3.10/dist-packages/altair/utils/schemapi.py:462: DeprecationWarning: jsonschema.RefResolver is deprecated as of v4.18.0, in favor of the https://github.com/python-jsonschema/referencing library, which provides more compliant referencing behavior as well as more flexible APIs for customization. A future release will remove RefResolver. Please file a feature request (on referencing) if you are missing an API for the kind of customization you n

In [ ]:
locations = list(zip(df['lat'], df['long']))
locations

Iteration 6: This map displays the information as a heat map

In [10]:
m = folium.Map(width=800,height=800,
               location=[47.6, -122.3],
               tiles='cartodbpositron',
               zoom_start=3, control_scale=True)

plugins.HeatMap(locations).add_to(m)
m

##Using OpenMap


I used this code to locate the city that had the school shooting with the most casualties: Parkland, Florida(Marjory Stoneman Douglas High School).

In [11]:
df[['casualties', 'city']].value_counts()

casualties  city       
1           Baltimore      5
            Chicago        5
            Memphis        4
            Houston        4
            Los Angeles    4
                          ..
            Alpine         1
            Albemarle      1
0           Woodbridge     1
            Westminster    1
34          Parkland       1
Length: 332, dtype: int64

I then used Open street Map to find all the schools in Florida and plotted the points below.

In [12]:
# get the geometry for Florida
Florida = ox.geocode_to_gdf('R162050', by_osmid = True)

amenities = ox.features_from_polygon(Florida["geometry"].iloc[0], tags={"amenity":['school']})

amenities = gpd.GeoDataFrame.from_features(amenities)
amenitypts = amenities[amenities.geom_type == 'Point']
amenitypts['long']=amenitypts['geometry'].x
amenitypts['lat']=amenitypts['geometry'].y
amenitypts.head()

/usr/local/lib/python3.10/dist-packages/osmnx/_overpass.py:211: UserWarning: This area is 141 times your configured Overpass max query area size. It will automatically be divided up into multiple sub-queries accordingly. This may take a long time.
  multi_poly_proj = utils_geo._consolidate_subdivide_geometry(poly_proj)
/usr/local/lib/python3.10/dist-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/usr/local/lib/python3.10/dist-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/

geometry amenity   ele gnis:county_id gnis:created  \
0   POINT (-81.65639 24.59656)  school     2            087   08/28/1987   
1   POINT (-81.79734 24.59361)  school  None           None         None   
12  POINT (-81.79342 26.16481)  school     2            021   10/19/1979   
13  POINT (-81.76955 26.18068)  school     2            021   08/28/1987   
14  POINT (-81.80814 26.18703)  school     0            021   08/28/1987   

   gnis:feature_id gnis:state_id                         name nodes addr:city  \
0           303760            12              Spectrum School  None      None   
1             None          None                 SFUWO School  None      None   
12          285270            12  Lake Park Elementary School  None      None   
13          297394            12  Poinciana Elementary School  None      None   
14          299701            12            Walden University  None      None   

    ... attribution name:es shortest_name long_name phone:main historic:name  \
0   ...        None    None          None      None       None          None   
1   ...        None    None          None      None       None          None   
12  ...        None    None          None      None       None          None   
13  ...        None    None          None      None       None          None   
14  ...        None    None          None      None       None          None   

   sport gnis:state_idgnis:state_id       long        lat  
0   None                       None -81.656386  24.596556  
1   None                       None -81.797344  24.593606  
12  None                       None -81.793421  26.164813  
13  None                       None -81.769555  26.180678  
14  None                       None -81.808144  26.187034  

[5 rows x 134 columns]

In [13]:
m = folium.Map(width=800,height=800,
               location=[26.304483, -80.269365],
               tiles='cartodbpositron',
               zoom_start=5, control_scale=True)
for idx, row in amenitypts.iterrows():
    # Get lat and lon of points
    lon = row['long']
    lat = row['lat']

    # get name for tooltip
    name = row['name']

    # Add marker to the map
    folium.Marker(location=[lat, lon],
                  tooltip=name
    ).add_to(m)
m



Then I used this code to find the nearest hospital to the location of the school shooting incident with the highest number of casualties

In [14]:
mypoint = [26.304483, -80.269365] # center point in lat lon
mydist = 4000 # distance in m

hospital = ox.features_from_point(center_point = mypoint,
                                     tags={"building":['hospital']},
                                     dist = mydist)

hospital = gpd.GeoDataFrame.from_features(hospital)
hospital['long']=hospital['geometry'].apply(lambda geom: geom.centroid.x if geom.geom_type == 'Point' else geom.exterior.coords.xy[0][0])
hospital['lat']=hospital['geometry'].apply(lambda geom: geom.centroid.x if geom.geom_type == 'Point' else geom.exterior.coords.xy[1][0])

/usr/local/lib/python3.10/dist-packages/pandas/core/dtypes/cast.py:1641: DeprecationWarning: np.find_common_type is deprecated.  Please use `np.result_type` or `np.promote_types`.
See https://numpy.org/devdocs/release/1.25.0-notes.html and the docs for more information.  (Deprecated NumPy 1.25)
  return np.find_common_type(types, [])
/usr/local/lib/python3.10/dist-packages/pandas/core/dtypes/cast.py:1641: DeprecationWarning: np.find_common_type is deprecated.  Please use `np.result_type` or `np.promote_types`.
See https://numpy.org/devdocs/release/1.25.0-notes.html and the docs for more information.  (Deprecated NumPy 1.25)
  return np.find_common_type(types, [])
/usr/local/lib/python3.10/dist-packages/pandas/core/algorithms.py:522: DeprecationWarning: np.find_common_type is deprecated.  Please use `np.result_type` or `np.promote_types`.
See https://numpy.org/devdocs/release/1.25.0-notes.html and the docs for more information.  (Deprecated NumPy 1.25)
  common = np.find_common_type([va

From this map, we can see that the nearest hospital was almost 4000m away from the Highschool in Parkland where this incidence took place.

In [15]:
m = folium.Map(width=800,height=800,
               location=mypoint,
               tiles='cartodbpositron',
               zoom_start=10, control_scale=True)
for idx, row in hospital.iterrows():
    # Get lat and lon of points
    lon = row['long']
    lat = row['lat']

    # Add marker to the map
    folium.Circle(location=[lat, lon],
                  radius = 2
    ).add_to(m)
m